# 1. Libraries etc.

## Libraries

In [1]:
import pandas as pd

In [2]:
import os
from math import sqrt
import pandas as pd
import numpy as np
import matplotlib
import multiprocessing
import itertools
import warnings
from pylab import rcParams
# sklearn
from sklearn.model_selection import cross_val_score, GroupKFold, StratifiedKFold, train_test_split, GridSearchCV, cross_validate
from sklearn.ensemble import RandomForestClassifier
from sklearn import metrics
from sklearn.calibration import calibration_curve
# IPython
from IPython.core.interactiveshell import InteractiveShell
from IPython.display import display
# Bokeh
from bokeh.plotting import figure, show, output_file, ColumnDataSource
from bokeh.layouts import column, gridplot
from bokeh.io import output_notebook
from bokeh.models.annotations import Label,LabelSet                  
from bokeh.models import Legend
from bokeh.models import LinearAxis, Range1d

In [3]:
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer

In [4]:
import sklearn
print(sklearn.__version__)

0.24.1


## Settings

In [5]:
warnings.filterwarnings('ignore')
multiprocessing.set_start_method('spawn', True)
InteractiveShell.ast_node_interactivity = "all"
#pd.set_option('display.max_colwidth',200)
#pd.set_option('display.max_rows', 500)
%matplotlib inline
cur_dir = os.path.dirname("__file__")

## Class : Status

For managing ICU data.

In [6]:
#========================================
#  class : status
#========================================
class status():
    def __init__(self, df):
        # df
        self.df = df
        self.df_thistime = pd.DataFrame([], columns=df.columns)
        self.df_next = df
        # ID
        self.ids_all = set(df.patientunitstayid)
        self.ids_thistime = set([])
        self.ids_next = self.ids_all
        # parameter
        self.target = []
        
        
    def remove(self, target):
        self.target += target
        # Update ID
        tmp = set(self.df_next.drop(target, axis=1).where(self.df_next>=0).dropna().patientunitstayid)
        self.ids_thistime |= tmp
        self.ids_next -= tmp
        
        # df thistime
        self.df_thistime = self.df.drop(self.target, axis=1)
        self.df_thistime = self.df_thistime.query("patientunitstayid in @ self.ids_thistime")
        
        # df_next
        self.df_next = self.df_next.drop(target, axis=1)
        self.df_next = self.df_next.query("patientunitstayid in @ self.ids_next")
        
        
    def get_next(self, depth):
        # 1st and Last columns are not paramters
        parameters = self.df_next.columns[1:-1]
        
        # depth : the number of parameters to be excluded at once
        combinations = [list(i) for i in itertools.combinations(parameters, depth)]
        
        # # of non-NaN-records 
        num_non_nan = pd.DataFrame({
            "__".join(comb) : [len(self.df_next.drop(comb, axis=1).where(self.df_next>=0).dropna())]
            for comb in combinations
        }).T
        
        # "1 <= # of non-NaN-records < # of pids" is ideal.
        tf = num_non_nan.applymap(lambda x : 1 <= x <= len(self.df_next) - 1)        
        if tf.any().any():
            tmp = num_non_nan[tf]
            return tmp.idxmax()[0]
        
        else:
            # "# of non-NaN-records == # of pids" is acceptable.
            tf = num_non_nan.applymap(lambda x : 1 <= x <= len(self.df_next))
            if tf.any().any():
                tmp = num_non_nan[tf]
                return tmp.idxmax()[0]
            
            else:
                # If there's no more parameteres, return nan      
                if len(parameters) == 1:
                    return "nan"

                # If there's only NaN records, return ""
                else:
                    return ""
                

## Training Data and Test Data

In [7]:
#========================================
# Split 
#========================================
def pid_train_test_split(df_A):
    # df_A  -->  pid_X and y
    length = len(df_A.columns)
    pid_X = df_A.iloc[:, : length-1].values
    y = df_A.iloc[:, -1].values

    pid_X_train, pid_X_test, y_train, y_test = split_stratified(pid_X, y)

    length = pid_X_train.shape[1]
    X_train = pid_X_train[:, 1:length]
    X_test = pid_X_test[:, 1:length]
    pid_train = pid_X_train[:, 0]
    pid_test = pid_X_test[:, 0]
    
    
    # Return as Dictionary
    dataset = {
        "pid_train" : pid_train,
        "pid_test" : pid_test,
        "X_train" : X_train,
        "X_test" : X_test,
        "y_train" : y_train,
        "y_test" : y_test
    }    
    return dataset



#========================================
#  StratifiedKFold Split
#========================================
def split_stratified(pid_X, y):
    skfold = StratifiedKFold(n_splits=5, shuffle=True)
    index = [i for i in skfold.split(pid_X, y)]
    train_index = index[0][0]
    test_index = index[0][1]
    pid_X_train = pid_X[train_index,:]
    pid_X_test = pid_X[test_index,:]
    y_train = y[train_index]
    y_test = y[test_index]
    return pid_X_train, pid_X_test, y_train, y_test

## Grid Search

In [8]:
#========================================
#  StratifiedKFold Grid Search
#========================================
def grid_search(X_train, y_train):
    skfold = StratifiedKFold(n_splits=5, shuffle=True)
    h_parms={
        "n_estimators" : [i for i in range(10,50,10)],
        "criterion" : ["gini","entropy"],
        "max_depth" : [i for i in range(1,6,1)],
        "random_state" : [123, 777, 2525]
    }
    rdm_gs = GridSearchCV(RandomForestClassifier(), param_grid=h_parms, cv=skfold, n_jobs=5)    
    rdm_gs.fit(X_train, y_train)
    h_parm = rdm_gs.best_estimator_.get_params(True).items()
    h_parm = {tup[0] : tup[1] for tup in h_parm}
    return h_parm


#========================================
#  Display Hyper Parameters
#========================================        
def disp(h_parm, switch):
    df = pd.DataFrame({key : [h_parm[key]] for key in h_parm.keys()}).T
    df.columns = ["Hypter Parameters"]
    print("--> Belows are selected.") 
    print("\n") 
    if switch ==0:
        display(df)
    else:
        display(df[["n_estimators", "criterion", "max_depth","random_state"]])
    print("\n") 
    

## Cross Validation

In [9]:
#========================================
#  Cross Validation
#========================================        
def cross_validation(h_parm, X_train, y_train):
    # Model
    rdm = RandomForestClassifier(
        n_estimators = h_parm["n_estimators"], 
        criterion = h_parm["criterion"],
        max_depth = h_parm["max_depth"], 
        random_state = h_parm["random_state"]
    )        
    # Split Criteria
    skfold = StratifiedKFold(n_splits=5, shuffle=True)
    # Cross Validation
    scores = cross_val_score(rdm, X_train, y_train, cv=skfold, scoring="accuracy")
    # Print Mean & STD
    score_mean = np.mean(scores)
    score_std = np.std(scores)    
    print(str(round(score_mean,5)) + ' ± ' + str(round(score_std,5)))
    

## Prediction

In [10]:
#========================================
#  Model Generation
#========================================        
def fitting(h_parm, X_train, y_train):
    rdm = RandomForestClassifier(
        n_estimators = h_parm["n_estimators"], 
        criterion = h_parm["criterion"],
        max_depth = h_parm["max_depth"], 
        random_state = h_parm["random_state"]
    )
    rdm.fit(X_train, y_train)      
    return rdm



#========================================
#  Prediction
#========================================        
def prediction(rdm, X_test):
    y_predicted = rdm.predict_proba(X_test)[:, 1]
    return y_predicted


## Evaluation : ROC & AUC

In [11]:
#========================================
#  Draw ROC
#========================================        
def roc_auc(y_test, y_predicted, y_test_IV, y_predicted_IV, y_test_IVa, y_predicted_IVa):
    
    # Ours
    fpr_ours, tpr_ours, thresholds = metrics.roc_curve(y_test, y_predicted, drop_intermediate=False)
    auc_ours = metrics.auc(fpr_ours, tpr_ours)

    # APACHE IV
    fpr_IV, tpr_IV, thresholds = metrics.roc_curve(y_test_IV, y_predicted_IV, drop_intermediate=False)
    auc_IV = metrics.auc(fpr_IV, tpr_IV)    

    # APACHE IVa
    fpr_IVa, tpr_IVa, thresholds = metrics.roc_curve(y_test_IVa, y_predicted_IVa, drop_intermediate=False)
    auc_IVa = metrics.auc(fpr_IVa, tpr_IVa)    

    # Ours + APACHE IV + APACHE IVa dataset for Bokeh
    source = ColumnDataSource(data=dict(
        x_ours = fpr_ours,
        y_ours = tpr_ours,    
        x_IV = fpr_IV,
        y_IV = tpr_IV,    
        x_IVa = fpr_IVa,
        y_IVa = tpr_IVa,    
    ))
    
    # Title, Size
    p = figure(
        title = 'ROC curve',
        plot_width=350,
        plot_height=350
    )
    
    # Axis Labels
    p.xaxis.axis_label = 'False Positive Rate'
    p.yaxis.axis_label = 'True Positive Rate'

    # Plot
    p.line('x_ours', 'y_ours', color='red', legend='Ours', line_width=2, source=source)
    p.line('x_IV', 'y_IV', color='green', legend='APACHE IV', line_width=2, source=source)
    p.line('x_IVa', 'y_IVa', color='blue', legend='APACHE IVa', line_width=2, source=source)

    # Legend
    p.legend.location = "bottom_right"
    p.legend.label_text_font_style = "bold"
    p.legend.label_text_font_size = "1pt"
    
    # Texts for AUC
    # "AUC"
    description=Label(
        x_offset=145,
        y_offset=145,
        x_units='screen',
        y_units='screen',
        text = 'AUC',
        text_font_size='1pt', render_mode="css"
    )        
    p.add_layout(description)    

    # AUC for Ours
    description=Label(
        x_offset=140,
        y_offset=130,
        x_units='screen',
        y_units='screen',
        text = '%.5f (Ours)'%auc_ours,
        text_font_size='1pt', render_mode="css"
    )        
    p.add_layout(description)    

    # AUC for APACHE IV
    description=Label(
        x_offset=140,
        y_offset=115,
        x_units='screen',
        y_units='screen',
        text = '%.5f (APACHE IV)'%auc_IV,
        text_font_size='1pt', render_mode="css"
    )        
    p.add_layout(description)    

    # AUC for APACHE IVa
    description=Label(
        x_offset=140,
        y_offset=100,
        x_units='screen',
        y_units='screen',
        text = '%.5f (APACHE IVa)'%auc_IVa,
        text_font_size='1pt', render_mode="css"
    )        
    p.add_layout(description)    
    
    # Output on the notebook
    output_notebook()    
    show(p)
    
    a = str(round(auc_ours,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_ours, np.array(y_test), np.array(y_predicted))])+"]"
    b = str(round(auc_IV,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_IV, np.array(y_test_IV), np.array(y_predicted_IV))])+"]"
    c = str(round(auc_IVa,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_IVa, np.array(y_test_IVa), np.array(y_predicted_IVa))])+"]"
    return [[a,b,c]]

## Evaluation : Confidence Interval for AUROC

In [12]:
#========================================
#  AUROC CI
#========================================        
def get_ci(auc, y_test, y_predicted):
    n1 = sum(y_test==1)
    n2 = sum(y_test!=1)
    q1 = auc / (2- auc)
    q2 = 2*auc**2 / (1+auc)
    se_auc = sqrt((auc*(1 - auc) + (n1 - 1)*(q1 - auc**2) + (n2 - 1)*(q2 - auc**2)) / (n1*n2))
    lower = auc - 1.96*se_auc
    upper = auc + 1.96*se_auc
    lower = 0 if lower <0 else lower
    upper = 1 if upper >1 else upper
    return lower, upper

## Evaluation : Comparison with APACHE system

In [13]:
#========================================
#  Draw scatter
#========================================
def plot_check(df_p):
    # DataFrame
#    apache_IV = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"][['patientunitstayid', 'predictedicumortality','actualicumortality']]
#    apache_IVa = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"][['patientunitstayid', 'predictedicumortality']]
    apache_IV = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IV"][['patientunitstayid', 'predictedicumortality','actualicumortality']]
    apache_IVa = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"][['patientunitstayid', 'predictedicumortality']]
    df_IV_IVa = pd.merge(apache_IV, apache_IVa, on="patientunitstayid")
    df_p_IV_IVa = pd.merge(df_IV_IVa, df_p, on="patientunitstayid")
    

    # Graph title
    graph_title = ["IV vs IVa", "IV vs Ours", "IVa vs Ours"]

    # Axis labels
    x_axis_label = ["APACHE IV", "APACHE IV", "APACHE IVa"]
    y_axis_label = ["APACHE IVa", "Ours", "Ours"]

    # Graph data
    x_data = [df_p_IV_IVa.predictedicumortality_x, df_p_IV_IVa.predictedicumortality_x, df_p_IV_IVa.predictedicumortality_y]
    y_data = [df_p_IV_IVa.predictedicumortality_y, df_p_IV_IVa.predictedicumortality, df_p_IV_IVa.predictedicumortality]
    
    # patientunitstayid
    pid = df_p_IV_IVa.patientunitstayid
    
    colormap = {'ALIVE': 'green', 'EXPIRED': 'red'}
    df_p_IV_IVa['color'] = df_p_IV_IVa['actualicumortality'].map(lambda x: colormap[x])

    
    output_notebook()

    p=[]
    p.append([])
    
    for i in range(3):
                    
        # Other configurations
        x_size = 300
        y_size = 300
        alpha = 0.2
        size = 4

        # graph objects
        source = ColumnDataSource(data=dict(
            x=x_data[i],
            y=y_data[i], 
            pid=pid,
            color=df_p_IV_IVa['color'],
            legend=df_p_IV_IVa['actualicumortality']
        ))
                
        TOOLTIPS = [("index", "$index"),("(x,y)", "($x, $y)"),("pid", "@pid")]

        p[-1].append(figure(
            title = graph_title[i],
            plot_width = x_size,
            plot_height = y_size,
            tooltips = TOOLTIPS,
            x_range=(0, 1),
            y_range=(0, 1)
        ))
        
        p[-1][-1].xaxis.axis_label = x_axis_label[i]
        p[-1][-1].yaxis.axis_label = y_axis_label[i]
        p[-1][-1].circle(
            'x', 'y',
            fill_color="color",
            line_color="color",
            fill_alpha=alpha,
            legend='legend',
            size=size,
            source=source
        )

        # Texts
        description=Label(
            x_offset=10,
            y_offset=210,
            x_units='screen',
            y_units='screen',
            text=str(len(pid)) + " of patients plotted",
            text_font_size='1pt', render_mode="css"
        )
        
        p[-1][-1].add_layout(description)    
        
        p[-1][-1].legend.location = "top_left"
        p[-1][-1].legend.label_text_font_style = "bold"
        p[-1][-1].legend.label_text_font_size = "1pt"
            
    grid = gridplot(p)
    show(grid)

## Evaluation : Calibration Plots

In [14]:
def calibration_plot(df_p):
    # DataFrame
    apache_IV = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IV"][['patientunitstayid', 'predictedicumortality','actualicumortality']]
    apache_IVa = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"][['patientunitstayid', 'predictedicumortality']]
    df_IV_IVa = pd.merge(apache_IV, apache_IVa, on="patientunitstayid")
    df_p_IV_IVa = pd.merge(df_IV_IVa, df_p, on="patientunitstayid")     # <- [pid, probBy_IV, actual_mortality, probBy_IVa, probBy_us]
    df_p_IV_IVa = df_p_IV_IVa.where(df_p_IV_IVa>=0).dropna()
    
    # Probability from Ours, IV and IVa
    probs = [df_p_IV_IVa.predictedicumortality, df_p_IV_IVa.predictedicumortality_x, df_p_IV_IVa.predictedicumortality_y]

    # Outcome
    numbermap = {'ALIVE': 0, 'EXPIRED': 1}
    outcome = df_p_IV_IVa['actualicumortality'].map(lambda x: numbermap[x])

    # Graph title
    graph_title = ["Ours", "IV", "IVa"]
    
    output_notebook()

    p=[]
    
    for i in range(3):

        p.append([])
                            
        # Data for Calibration Plot
        prob_true, prob_pred = calibration_curve(y_true=outcome, y_prob=probs[i], n_bins=10)

        # graph objects                
        p[-1].append(figure(
            title = graph_title[i],
            plot_width = 600,
            plot_height = 300,
            y_range=(0, 1.05)
        ))

        # Axis
        p[-1][-1].xaxis.axis_label = "Predicted Probability"
        p[-1][-1].yaxis.axis_label = "Actual Probability"

        # Plot              
        p1 =p[-1][-1].line(prob_pred, prob_true, line_width=2)
        p2 = p[-1][-1].circle(prob_pred, prob_true, fill_color="white", size=4)

        # Ideal
        p3 = p[-1][-1].line([0,1], [0,1], line_color="red", line_dash="dotted", line_width=2)
        
        # histogram
        hist, edges = np.histogram(probs[i], bins=10)
        p[-1][-1].extra_y_ranges = {"hist": Range1d(start=0, end=max(hist))}
        linaxis = LinearAxis(axis_label="# of cases", y_range_name='hist')
        p[-1][-1].add_layout(linaxis, 'right')
        p[-1][-1].quad(top=hist, bottom=0, left=edges[:-1], right=edges[1:], fill_color="navy", line_color="white", alpha=0.5, y_range_name="hist")
        
        
        # Legend        
        legend = Legend(items=[
            ("Calibration"   , [p1, p2]),
            ("Ideal" , [p3])
        ], location="bottom_right", label_text_font_style = "bold", label_text_font_size = "1pt")        
        p[-1][-1].add_layout(legend, 'right')
            
    grid = gridplot(p)
    show(grid)
    

# 2. Prepare DataFrame

## 2.1. Target IDs (4,226 cases)

In [15]:
input_ids = set(pd.read_csv("../ids/004_sepsis_aps_4226.csv", header=None).iloc[:,0].tolist())
len(input_ids)

4226

In [16]:
eICU_file = {}
eICU_file['apacheApsVar'] = pd.read_csv('../data/apacheApsVar.csv')
eICU_file['apachePatientResult'] = pd.read_csv('../data/apachePatientResult.csv')
eICU_file['apachePredVar'] = pd.read_csv('../data/apachePredVar.csv')
eICU_file['patient'] = pd.read_csv('../data/patient.csv')

In [17]:
eICU_parm = {}

eICU_parm['apacheApsVar'] = [
    'patientunitstayid', 'intubated', 'vent', 'dialysis', 'eyes', 'motor', 'verbal', 'meds', 'urine', 'wbc', 'temperature','respiratoryrate',
    'sodium', 'heartrate', 'meanbp', 'ph', 'hematocrit', 'creatinine', 'albumin', 'pao2', 'pco2', 'bun', 'glucose', 'bilirubin', 'fio2'
]

eICU_parm['apachePatientResult'] = [
    'patientunitstayid', 'apachescore', 'predictedicumortality', 'predictediculos', 'predictedhospitalmortality',
    'predictedhospitallos', 'preopmi', 'preopcardiaccath', 'ptcawithin24h', 'predventdays'
]

eICU_parm['apachePredVar'] = [
    'patientunitstayid', 'gender', 'teachtype', 'bedcount', 'graftcount', 'age', 'thrombolytics', 'aids', 'hepaticfailure', 'lymphoma',
    'metastaticcancer', 'leukemia', 'immunosuppression', 'cirrhosis', 'ima', 'midur', 'ventday1', 'oobventday1', 'oobintubday1', 'diabetes'
]

eICU_parm['patient'] = [
    'patientunitstayid', 'hospitalid', 'admissionheight', 'hospitaladmitoffset', 'admissionweight'
]

## DataFrame

In [18]:
#========================================
#  select columns and ids for each file
#========================================
eICU_df = {}
eICU_df['apacheApsVar'] = eICU_file['apacheApsVar'][eICU_parm['apacheApsVar']].query("patientunitstayid in @ input_ids") 
eICU_df['apachePatientResult'] = eICU_file['apachePatientResult'][eICU_parm['apachePatientResult']].query("patientunitstayid in @ input_ids") 
eICU_df['apachePredVar'] = eICU_file['apachePredVar'][eICU_parm['apachePredVar']].query("patientunitstayid in @ input_ids") 
eICU_df['patient'] = eICU_file['patient'][eICU_parm['patient']].query("patientunitstayid in @ input_ids") 


#========================================
#  make column names unique
#========================================
#  (column name -> filename + column name)
eICU_df['apacheApsVar'].columns = [
    'apacheApsVar_' + parm if not parm=="patientunitstayid" else "patientunitstayid"
    for parm in eICU_df['apacheApsVar'].columns
]
eICU_df['apachePatientResult'].columns = [
    'apachePatientResult_' + parm if not parm=="patientunitstayid" else "patientunitstayid"
    for parm in eICU_df['apachePatientResult'].columns
]
eICU_df['apachePredVar'].columns = [
    'apachePredVar_' + parm if not parm=="patientunitstayid" else "patientunitstayid"
    for parm in eICU_df['apachePredVar'].columns
]
eICU_df['patient'].columns = [
    'patient_' + parm if not parm=="patientunitstayid" else "patientunitstayid"
    for parm in eICU_df['patient'].columns
]


#========================================
#  Make X
#========================================
# 1st column : key (patientunitstayid)
key = pd.DataFrame(list(input_ids), columns=["patientunitstayid"])

# 2nd~ column : parameters
key_X = pd.merge(key, eICU_df['apacheApsVar'], on="patientunitstayid")
key_X = pd.merge(key_X, eICU_df['apachePatientResult'], on="patientunitstayid")
key_X = pd.merge(key_X, eICU_df['apachePredVar'], on="patientunitstayid")
key_X = pd.merge(key_X, eICU_df['patient'], on="patientunitstayid")


#========================================
#  Make X_y (df)
#========================================
# Last column : DEAD(=1) or ALIVE(=0)
y = eICU_file["apachePatientResult"][['patientunitstayid', 'actualicumortality']].replace('ALIVE',0).replace('EXPIRED',1)
key_X_y = pd.merge(key_X, y, on="patientunitstayid")

# Rename
df = key_X_y

# 4. Running

In [19]:
#========================================
#  Initialization
#========================================
df_status = status(df)
k=1
t_y_test, t_y_predicted, t_y_test_IV, t_y_predicted_IV, t_y_test_IVa, t_y_predicted_IVa = [],[],[],[],[],[]
t_pid_test, t_y_predicted = [], []
df_ci = []

print("# of INPUT : ", len(df_status.ids_all), " patientunitstayids", "\n\n")

while 1:
    print("##################################")
    print("                          Subgroup ",k) 
    print("##################################")
    print("\n") 
    print("Checking the inputs...")
    print("\n") 

    
    
    parms_tobe_excluded = []
    
    #========================================
    #  Get Subgroup
    #========================================
    while not(500 <= len(df_status.ids_thistime) <= 2000):

        parms = ""

        # upto 3 parameters taken into account
        for i in range(1,4):
            parms = df_status.get_next(i)

            # if parameters are found
            if parms != "":
                break
                

        # If no paramteres found, Output "Time out" and Stop.
        if parms == "":
            print("Time Out\n")
            df_status.df_next = pd.DataFrame()
            break
            
        # If too many nan, Output "Interpolation needed" and Stop
        if parms == "nan":
            print("Interpolation needed\n")
            df_status.df_next = pd.DataFrame()
            break

            
        # Change format
        parms = parms.split("__")        

        # Update
        df_status.remove(parms)
        parms_tobe_excluded += parms
        print("--> ", [i.split("_")[1] for i in parms], " is/are selected to be excluded.\n")
        
  

    print("--> ", ", ".join([i.split("_")[1] for i in parms_tobe_excluded]), " was/were excluded in the end.\n")
    parms_tobe_excluded = []

    
    
    df_A = pd.DataFrame()
    
    if 500 <= len(df_status.ids_next):
        print("--> ", len(df_status.ids_thistime), " patientunitstayids survived.\n")
        df_A = df_status.df_thistime
        df_status = status(df_status.df_next)
        
    else:
        # The rests pids are picked up and merged into thistime.
        print("--> ", len(df_status.ids_thistime)+len(df_status.ids_next), " patientunitstayids survived.\n")
        df_A = pd.concat([df_status.df_thistime, df_status.df_next])
        df_status.ids_next = set([])
        df_status.df_next = df_status.df_next.query("patientunitstayid in @ df_status.ids_next")
        
    df_A = df_A.where(df_A>=0).dropna()

    


    #========================================
    #  Learning
    #========================================    
    # Prepare Trainind data and Test Data
    dataset = pid_train_test_split(df_A)
    X_train = dataset["X_train"]
    y_train = dataset["y_train"]
    X_test = dataset["X_test"]
    y_test = dataset["y_test"]
    pid_test = dataset["pid_test"]

    # Grid Search
    h_parm = grid_search(X_train, y_train)
    
    # Cross Validation
    cross_validation(h_parm, X_train, y_train)

    # Model Generation
    rdm = fitting(h_parm, X_train, y_train)

    # Prediction
    y_predicted = prediction(rdm, X_test)

    
    
    #========================================
    #  Evaluation
    #========================================    
    # Prediction by APACHE
    df_apache = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IV"].query("patientunitstayid in @ pid_test")
    id_IV = df_apache[df_apache["apacheversion"]=="IV"]['patientunitstayid'].values.tolist()
    y_test_IV = df_apache.query("patientunitstayid in @ id_IV").actualicumortality.replace('ALIVE',0).replace('EXPIRED',1).values.tolist()
    y_predicted_IV = df_apache.query("patientunitstayid in @ id_IV").predictedicumortality.values.tolist()

    df_apache = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"].query("patientunitstayid in @ pid_test")
    id_IVa = df_apache[df_apache["apacheversion"]=="IVa"]['patientunitstayid'].values.tolist()
    y_test_IVa = df_apache.query("patientunitstayid in @ id_IVa").actualicumortality.replace('ALIVE',0).replace('EXPIRED',1).values.tolist()
    y_predicted_IVa = df_apache.query("patientunitstayid in @ id_IVa").predictedicumortality.values.tolist()
    
    
    # Store subgroup information
    t_y_test += list(y_test)
    t_y_predicted += list(y_predicted)
    t_y_test_IV += list(y_test_IV)
    t_y_predicted_IV += list(y_predicted_IV)
    t_y_test_IVa += list(y_test_IVa)
    t_y_predicted_IVa += list(y_predicted_IVa)
    t_pid_test += pid_test.tolist()
    
    
    # ROC and AUC
    df_ci += roc_auc(y_test, y_predicted, y_test_IV, y_predicted_IV, y_test_IVa, y_predicted_IVa)
        
    # Comparison with APACHE
    df_p = pd.DataFrame([pid_test.tolist(), y_predicted.tolist()]).T
    df_p.columns = ["patientunitstayid","predictedicumortality"]
    plot_check(df_p)

    # Calibration Plots
    calibration_plot(df_p)
    
    k+=1
    
    if len(df_status.df_next) ==  0:
        break

        

        
print("##################################")
print("                          Overall (Integrated)") 
print("##################################")

# ROC and AUC
df_ci += roc_auc(t_y_test, t_y_predicted, t_y_test_IV, t_y_predicted_IV, t_y_test_IVa, t_y_predicted_IVa)

# Comparison with APACHE
df_p = pd.DataFrame([t_pid_test, t_y_predicted]).T
df_p.columns = ["patientunitstayid","predictedicumortality"]
plot_check(df_p)

# Calibration Plots
calibration_plot(df_p)


# Confidence Interval
df_ci = pd.DataFrame(df_ci, columns=["Ours","Apache IV","Apache IVa"], index=["1","2","3","4","5","ALL"])
df_ci

# of INPUT :  4226  patientunitstayids 


##################################
                          Subgroup  1
##################################


Checking the inputs...


-->  ['hospitaladmitoffset']  is/are selected to be excluded.

-->  hospitaladmitoffset  was/were excluded in the end.

-->  884  patientunitstayids survived.

0.85325 ± 0.01048


Loading BokehJS ...

Loading BokehJS ...

Loading BokehJS ...

##################################
                          Subgroup  2
##################################


Checking the inputs...


-->  ['urine']  is/are selected to be excluded.

-->  urine  was/were excluded in the end.

-->  1037  patientunitstayids survived.

0.83724 ± 0.01088


...

##################################
                          Overall (Integrated)
##################################


Loading BokehJS ...

Loading BokehJS ...

Loading BokehJS ...

Ours            Apache IV           Apache IVa
1     0.88 [0.845,0.916]   0.76 [0.707,0.814]  0.756 [0.702,0.809]
2     0.88 [0.848,0.913]   0.77 [0.722,0.818]  0.763 [0.715,0.812]
3        0.964 [0.926,1]  0.788 [0.693,0.883]    0.808 [0.716,0.9]
4      0.9 [0.867,0.932]  0.814 [0.767,0.862]  0.815 [0.768,0.862]
5    0.912 [0.871,0.952]   0.77 [0.701,0.838]   0.77 [0.701,0.838]
ALL  0.903 [0.887,0.919]  0.788 [0.763,0.813]  0.788 [0.763,0.813]

## Imputation

In [20]:
#========================================
#  Save the above
#========================================
pre_df_ci = df_ci
pre_df_p = df_p
pre_y_test, pre_y_predicted = t_y_test, t_y_predicted
pre_pid = t_pid_test

#========================================
#  Imputation for X
#========================================
# Imputation for nan
imp = IterativeImputer(max_iter=10, random_state=0)
imp.fit(key_X)
imputated_key_X = imp.transform(key_X)
# Imputation for -1
imp = IterativeImputer(max_iter=10, random_state=0, missing_values=-1)
imp.fit(imputated_key_X)
imputated_key_X = imp.transform(imputated_key_X)
# Make DataFrame
key_X = pd.DataFrame(imputated_key_X, columns=key_X.columns)


#========================================
#  Make X_y (df)
#========================================
# Last column : DEAD(=1) or ALIVE(=0)
y = eICU_file["apachePatientResult"][['patientunitstayid', 'actualicumortality']].replace('ALIVE',0).replace('EXPIRED',1)
key_X_y = pd.merge(key_X, y, on="patientunitstayid")

# Rename
df = key_X_y



#========================================
#  Initialization
#========================================
df_status = status(df)
df_ci = []

print("# of INPUT : ", len(df_status.ids_all), " patientunitstayids", "\n\n")
    

df_A = df

#========================================
#  Learning
#========================================    
# Prepare Trainind data and Test Data
dataset = pid_train_test_split(df_A)
X_train = dataset["X_train"]
y_train = dataset["y_train"]
X_test = dataset["X_test"]
y_test = dataset["y_test"]
pid_test = dataset["pid_test"]

# Grid Search
h_parm = grid_search(X_train, y_train)
    
# Cross Validation
cross_validation(h_parm, X_train, y_train)

# Model Generation
rdm = fitting(h_parm, X_train, y_train)

# Prediction
y_predicted = prediction(rdm, X_test)

    
    
#========================================
#  Evaluation
#========================================    
# Prediction by APACHE
df_apache = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IV"].query("patientunitstayid in @ pid_test")
id_IV = df_apache[df_apache["apacheversion"]=="IV"]['patientunitstayid'].values.tolist()
y_test_IV = df_apache.query("patientunitstayid in @ id_IV").actualicumortality.replace('ALIVE',0).replace('EXPIRED',1).values.tolist()
y_predicted_IV = df_apache.query("patientunitstayid in @ id_IV").predictedicumortality.values.tolist()

df_apache = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"].query("patientunitstayid in @ pid_test")
id_IVa = df_apache[df_apache["apacheversion"]=="IVa"]['patientunitstayid'].values.tolist()
y_test_IVa = df_apache.query("patientunitstayid in @ id_IVa").actualicumortality.replace('ALIVE',0).replace('EXPIRED',1).values.tolist()
y_predicted_IVa = df_apache.query("patientunitstayid in @ id_IVa").predictedicumortality.values.tolist()
            

    
#========================================
#  Draw all ROC
#========================================        
# Imputation
fpr_imp, tpr_imp, thresholds = metrics.roc_curve(y_test, y_predicted, drop_intermediate=False)
auc_imp = metrics.auc(fpr_imp, tpr_imp)
# Ours
fpr_ours, tpr_ours, thresholds = metrics.roc_curve(pre_y_test, pre_y_predicted, drop_intermediate=False)
auc_ours = metrics.auc(fpr_ours, tpr_ours)
# APACHE IV
fpr_IV, tpr_IV, thresholds = metrics.roc_curve(y_test_IV, y_predicted_IV, drop_intermediate=False)
auc_IV = metrics.auc(fpr_IV, tpr_IV)    
# APACHE IVa
fpr_IVa, tpr_IVa, thresholds = metrics.roc_curve(y_test_IVa, y_predicted_IVa, drop_intermediate=False)
auc_IVa = metrics.auc(fpr_IVa, tpr_IVa)    

# Ours + APACHE IV + APACHE IVa dataset for Bokeh
source = ColumnDataSource(data=dict(
    x_imp = fpr_imp,
    y_imp = tpr_imp,    
    x_ours = fpr_ours,
    y_ours = tpr_ours,    
    x_IV = fpr_IV,
    y_IV = tpr_IV,    
    x_IVa = fpr_IVa,
    y_IVa = tpr_IVa,    
))
    
# Title, Size
p = figure(
    title = 'ROC curve',
    plot_width=350,
    plot_height=350
)
    
# Axis Labels
p.xaxis.axis_label = 'False Positive Rate'
p.yaxis.axis_label = 'True Positive Rate'

# Plot
p.line('x_imp', 'y_imp', color='orange', legend='Imputation', line_width=2, source=source)
p.line('x_ours', 'y_ours', color='red', legend='Ours', line_width=2, source=source)
p.line('x_IV', 'y_IV', color='green', legend='APACHE IV', line_width=2, source=source)
p.line('x_IVa', 'y_IVa', color='blue', legend='APACHE IVa', line_width=2, source=source)

# Legend
p.legend.location = "bottom_right"
p.legend.label_text_font_style = "bold"
p.legend.label_text_font_size = "1pt"
    
# Texts for AUC
# "AUC"
description=Label(
    x_offset=145,
    y_offset=165,
    x_units='screen',
    y_units='screen',
    text = 'AUC',
    text_font_size='1pt', render_mode="css"
)        
p.add_layout(description)    
# AUC for Ours
description=Label(
    x_offset=140,
    y_offset=150,
    x_units='screen',
    y_units='screen',
    text = '%.5f (Ours)'%auc_ours,
    text_font_size='1pt', render_mode="css"
)        
p.add_layout(description)    
# AUC for Imputation
description=Label(
    x_offset=140,
    y_offset=135,
    x_units='screen',
    y_units='screen',
    text = '%.5f (Imputation)'%auc_imp,
    text_font_size='1pt', render_mode="css"
)        
p.add_layout(description)    
# AUC for APACHE IV
description=Label(
x_offset=140,
    y_offset=120,
    x_units='screen',
    y_units='screen',
    text = '%.5f (APACHE IV)'%auc_IV,
    text_font_size='1pt', render_mode="css"
)        
p.add_layout(description)    
# AUC for APACHE IVa
description=Label(
    x_offset=140,
    y_offset=105,
    x_units='screen',
    y_units='screen',
    text = '%.5f (APACHE IVa)'%auc_IVa,
    text_font_size='1pt', render_mode="css"
)        
p.add_layout(description)    
    
# Output on the notebook
output_notebook()    
show(p)
    

# Confidence Interval
a = str(round(auc_ours,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_ours, np.array(pre_y_test), np.array(pre_y_predicted))])+"]"
d = str(round(auc_imp,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_imp, np.array(y_test), np.array(y_predicted))])+"]"
b = str(round(auc_IV,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_IV, np.array(y_test_IV), np.array(y_predicted_IV))])+"]"
c = str(round(auc_IVa,3)) + " [" + ",".join([str(round(i,3)) for i in get_ci(auc_IVa, np.array(y_test_IVa), np.array(y_predicted_IVa))])+"]"
df_ci = [[a,d, b,c]]

IterativeImputer(random_state=0)

IterativeImputer(missing_values=-1, random_state=0)

# of INPUT :  4226  patientunitstayids 


0.84109 ± 0.00322


bokeh.models.renderers.GlyphRenderer(
    id='1cc62932-5ccd-49ce-a4ec-2e4b9d94827d',
    data_source=bokeh.models.sources.ColumnDataSource(
        id='327d1591-e4d0-434b-9c9f-7540734f2865',
        callback=None,
        data={'y_ours': {'__ndarray__': 'AAAAAAAAAADTGDCNAdNYP9MYMI0B02g/nhLkKUGecj/TGDCNAdN4PwgffPDBB38/nhLkKUGegj+5FYpbobiFP9MYMI0B04g/7RvWvmHtiz8IH3zwwQePP54S5ClBnpI/KxS3QnErlD9GF1100UWXP9MYMI0B05g/YBoDpjFgmj/tG9a+Ye2bP3sdqdeRep0/CB988MEHnz9KkKcEeUqgPxEREREREaE/2JF6HanXoT+eEuQpQZ6iP2WTTTbZZKM/KxS3QnErpD/ylCBPCfKkP7kViluhuKU/f5bzZzl/pj9GF1100UWnPwyYxoBpDKg/0xgwjQHTqD9gGgOmMWCqPyebbLLJJqs/7RvWvmHtqz+0nD/L+bOsP3sdqdeReq0/zp/l/FnOrz9KkKcEeUqwPxEREREREbE/dNFFF110sT/YkXodqdexPztSryP1OrI/AtMYMI0Bsz9lk0022WSzP8hTgjwlyLM/KxS3QnErtD+P1OtIvY60P/KUIE8J8rQ/VVVVVVVVtT+5FYpbobi1P3+W82c5f7Y/41YoboXitj9GF1100UW3P6nXkXodqbc/DJjGgGkMuD9wWPuGtW+4P9MYMI0B07g/Ntlkk002uT+amZmZmZm5P2AaA6YxYLo/w9o3rH3Duj8nm2yyySa7P4pbobgVirs/7RvWvmHtuz9R3ArFrVC8P7ScP8v5s7w/F1100UUXvT97HanXkXq9P97d3d3d3b0/QZ4S5ClBvj+kXkfqdaS+PwgffPDBB78/a9+w9g1rvz/On+X8Wc6/P0qQpwR5SsA/fPDBBx98wD+uUNwKxa3AP9+w9g1r38A/ERERERERwT9DcSsUt0LBP3TRRRdddME/pjFgGgOmwT/YkXodqdfBPwnylCBPCcI/O1KvI/U6wj9tsskmm2zCP54S5ClBnsI/0HL+LOfPwj8C0xgwjQHDPzMzMzMzM8M/ZZNNNtlkwz/IU4I8JcjDP/qznD/L+cM/KxS3QnErxD9ddNFFF13EP4/U60i9jsQ/wDQGTGPAxD/ylCBPCfLEPyT1OlKvI8U/VVVVVVVVxT+HtW9Y+4bFP7kViluhuMU/6nWkXkfqxT8c1r5h7RvGP0422WSTTcY/f5bzZzl/xj+x9g1r37DGP+NWKG6F4sY/FLdCcSsUxz9GF1100UXHP6nXkXodqcc/2zesfcPaxz8MmMaAaQzIPz744IMPPsg/cFj7hrVvyD+huBWKW6HIP9MYMI0B08g/BXlKkKcEyT822WSTTTbJP2g5f5bzZ8k/aDl/lvNnyT+amZmZmZnJP8v5s5w/y8k//VnOn+X8yT8vuuiiiy7KP2AaA6YxYMo/knodqdeRyj/D2jesfcPKP/U6Uq8j9co/J5tssskmyz9Y+4a1b1jLP4pbobgViss/vLu7u7u7yz/tG9a+Ye3LPx988MEHH8w/UdwKxa1QzD+CPCXIU4LMP7ScP8v5s8w/5vxZzp/lzD8XXXTRRRfNP0m9jtTrSM0/ex2p15F6zT+sfcPaN6zNP97d3d3d3c0/ED744IMPzj9BnhLkKUHOP3P+LOfPcs4/pF5H6nWkzj/WvmHtG9bOPwgffPDBB88/OX+W82c5zz9r37D2DWvPP50/y/mznM8/zp/l/FnOzz8AAAAAAADQPxkwjQHTGNA/MmAaA6Yx0D9KkKcEeUrQP2PANAZMY9A/Y8A0Bkxj0D988MEHH3zQP5UgTwnylNA/lSBPCfKU0D+uUNwKxa3QP8eAaQyYxtA/37D2DWvf0D/44IMPPvjQP/jggw8++NA/ERERERER0T8RERERERHRPypBnhLkKdE/Q3ErFLdC0T9cobgVilvRP3TRRRdddNE/jQHTGDCN0T+mMWAaA6bRP79h7RvWvtE/2JF6HanX0T8J8pQgTwnSP1SCPCXIU9I/bbLJJpts0j+F4lYoboXSP54S5ClBntI/0HL+LOfP0j/poosuuujSPwLTGDCNAdM/GgOmMWAa0z8aA6YxYBrTPzMzMzMzM9M/TGPANAZM0z9MY8A0BkzTP2WTTTbZZNM/fsPaN6x90z+vI/U6Uq/TP8hTgjwlyNM/4YMPPvjg0z/6s5w/y/nTPxPkKUGeEtQ/KxS3QnEr1D9ERERERETUP0RERERERNQ/XXTRRRdd1D92pF5H6nXUP6gEeUqQp9Q/wDQGTGPA1D/ANAZMY8DUP9lkk0022dQ/8pQgTwny1D8Lxa1Q3ArVPyT1OlKvI9U/PSXIU4I81T89JchTgjzVP1VVVVVVVdU/boXiVihu1T9uheJWKG7VP4e1b1j7htU/oOX8Wc6f1T+g5fxZzp/VP7kViluhuNU/0UUXXXTR1T/qdaReR+rVPwOmMWAaA9Y/HNa+Ye0b1j9ONtlkk03WP2ZmZmZmZtY/ZmZmZmZm1j9mZmZmZmbWP3+W82c5f9Y/mMaAaQyY1j/jVihuheLWP/uGtW9Y+9Y/FLdCcSsU1z8t589y/izXP0YXXXTRRdc/X0fqdaRe1z93d3d3d3fXP5CnBHlKkNc/qdeReh2p1z/CBx988MHXP8IHH3zwwdc/2zesfcPa1z/0Zzl/lvPXPwyYxoBpDNg/JchTgjwl2D8++OCDDz7YP3BY+4a1b9g/iYiIiIiI2D+66KKLLrrYP7rooosuutg/0xgwjQHT2D/sSL2O1OvYPwV5SpCnBNk/HanXkXod2T822WSTTTbZP08J8pQgT9k/TwnylCBP2T+BaQyYxoDZP5qZmZmZmdk/y/mznD/L2T/9Wc6f5fzZP/1Zzp/l/Nk/FopbobgV2j8vuuiiiy7aPy+66KKLLto/L7rooosu2j8vuuiiiy7aP0fqdaReR9o/YBoDpjFg2j+Seh2p15HaP6uqqqqqqto/w9o3rH3D2j/1OlKvI/XaPw5r37D2Dds/QMv5s5w/2z9Y+4a1b1jbP1j7hrVvWNs/WPuGtW9Y2z9xKxS3QnHbP4pbobgVits/o4suuuii2z/V60i9jtTbPwZMY8A0Btw/BkxjwDQG3D8ffPDBBx/cPzisfcPaN9w/UdwKxa1Q3D9qDJjGgGncP5tssskmm9w/m2yyySab3D+bbLLJJpvcP7ScP8v5s9w/tJw/y/mz3D+0nD/L+bPcP83MzMzMzNw/5vxZzp/l3D/+LOfPcv7cPxdddNFFF90/F1100UUX3T8wjQHTGDDdP0m9jtTrSN0/ex2p15F63T97HanXkXrdP5NNNtlkk90/rH3D2jes3T+sfcPaN6zdP8WtUNwKxd0/xa1Q3ArF3T/FrVDcCsXdP8WtUNwKxd0/3t3d3d3d3T/3DWvfsPbdPxA++OCDD94/KG6F4lYo3j8oboXiVijeP0GeEuQpQd4/c/4s589y3j+MLrroooveP4wuuuiii94/pF5H6nWk3j+9jtTrSL3eP9a+Ye0b1t4/1r5h7RvW3j/v7u7u7u7eP+/u7u7u7t4/7+7u7u7u3j8IH3zwwQffPyFPCfKUIN8/IU8J8pQg3z8hTwnylCDfPzl/lvNnOd8/OX+W82c53z9SryP1OlLfP1KvI/U6Ut8/a9+w9g1r3z+dP8v5s5zfP50/y/mznN8/tm9Y+4a13z/nz3L+LOffP+fPcv4s598/DJjGgGkM4D8ZMI0B0xjgPzJgGgOmMeA/MmAaA6Yx4D8++OCDDz7gPz744IMPPuA/SpCnBHlK4D9KkKcEeUrgP1coboXiVuA/VyhuheJW4D9XKG6F4lbgP1coboXiVuA/Y

bokeh.models.renderers.GlyphRenderer(
    id='e36a7dc9-ad47-4a12-9aa6-c34aeee2523c',
    data_source=bokeh.models.sources.ColumnDataSource(
        id='327d1591-e4d0-434b-9c9f-7540734f2865',
        callback=None,
        data={'y_ours': {'__ndarray__': 'AAAAAAAAAADTGDCNAdNYP9MYMI0B02g/nhLkKUGecj/TGDCNAdN4PwgffPDBB38/nhLkKUGegj+5FYpbobiFP9MYMI0B04g/7RvWvmHtiz8IH3zwwQePP54S5ClBnpI/KxS3QnErlD9GF1100UWXP9MYMI0B05g/YBoDpjFgmj/tG9a+Ye2bP3sdqdeRep0/CB988MEHnz9KkKcEeUqgPxEREREREaE/2JF6HanXoT+eEuQpQZ6iP2WTTTbZZKM/KxS3QnErpD/ylCBPCfKkP7kViluhuKU/f5bzZzl/pj9GF1100UWnPwyYxoBpDKg/0xgwjQHTqD9gGgOmMWCqPyebbLLJJqs/7RvWvmHtqz+0nD/L+bOsP3sdqdeReq0/zp/l/FnOrz9KkKcEeUqwPxEREREREbE/dNFFF110sT/YkXodqdexPztSryP1OrI/AtMYMI0Bsz9lk0022WSzP8hTgjwlyLM/KxS3QnErtD+P1OtIvY60P/KUIE8J8rQ/VVVVVVVVtT+5FYpbobi1P3+W82c5f7Y/41YoboXitj9GF1100UW3P6nXkXodqbc/DJjGgGkMuD9wWPuGtW+4P9MYMI0B07g/Ntlkk002uT+amZmZmZm5P2AaA6YxYLo/w9o3rH3Duj8nm2yyySa7P4pbobgVirs/7RvWvmHtuz9R3ArFrVC8P7ScP8v5s7w/F1100UUXvT97HanXkXq9P97d3d3d3b0/QZ4S5ClBvj+kXkfqdaS+PwgffPDBB78/a9+w9g1rvz/On+X8Wc6/P0qQpwR5SsA/fPDBBx98wD+uUNwKxa3AP9+w9g1r38A/ERERERERwT9DcSsUt0LBP3TRRRdddME/pjFgGgOmwT/YkXodqdfBPwnylCBPCcI/O1KvI/U6wj9tsskmm2zCP54S5ClBnsI/0HL+LOfPwj8C0xgwjQHDPzMzMzMzM8M/ZZNNNtlkwz/IU4I8JcjDP/qznD/L+cM/KxS3QnErxD9ddNFFF13EP4/U60i9jsQ/wDQGTGPAxD/ylCBPCfLEPyT1OlKvI8U/VVVVVVVVxT+HtW9Y+4bFP7kViluhuMU/6nWkXkfqxT8c1r5h7RvGP0422WSTTcY/f5bzZzl/xj+x9g1r37DGP+NWKG6F4sY/FLdCcSsUxz9GF1100UXHP6nXkXodqcc/2zesfcPaxz8MmMaAaQzIPz744IMPPsg/cFj7hrVvyD+huBWKW6HIP9MYMI0B08g/BXlKkKcEyT822WSTTTbJP2g5f5bzZ8k/aDl/lvNnyT+amZmZmZnJP8v5s5w/y8k//VnOn+X8yT8vuuiiiy7KP2AaA6YxYMo/knodqdeRyj/D2jesfcPKP/U6Uq8j9co/J5tssskmyz9Y+4a1b1jLP4pbobgViss/vLu7u7u7yz/tG9a+Ye3LPx988MEHH8w/UdwKxa1QzD+CPCXIU4LMP7ScP8v5s8w/5vxZzp/lzD8XXXTRRRfNP0m9jtTrSM0/ex2p15F6zT+sfcPaN6zNP97d3d3d3c0/ED744IMPzj9BnhLkKUHOP3P+LOfPcs4/pF5H6nWkzj/WvmHtG9bOPwgffPDBB88/OX+W82c5zz9r37D2DWvPP50/y/mznM8/zp/l/FnOzz8AAAAAAADQPxkwjQHTGNA/MmAaA6Yx0D9KkKcEeUrQP2PANAZMY9A/Y8A0Bkxj0D988MEHH3zQP5UgTwnylNA/lSBPCfKU0D+uUNwKxa3QP8eAaQyYxtA/37D2DWvf0D/44IMPPvjQP/jggw8++NA/ERERERER0T8RERERERHRPypBnhLkKdE/Q3ErFLdC0T9cobgVilvRP3TRRRdddNE/jQHTGDCN0T+mMWAaA6bRP79h7RvWvtE/2JF6HanX0T8J8pQgTwnSP1SCPCXIU9I/bbLJJpts0j+F4lYoboXSP54S5ClBntI/0HL+LOfP0j/poosuuujSPwLTGDCNAdM/GgOmMWAa0z8aA6YxYBrTPzMzMzMzM9M/TGPANAZM0z9MY8A0BkzTP2WTTTbZZNM/fsPaN6x90z+vI/U6Uq/TP8hTgjwlyNM/4YMPPvjg0z/6s5w/y/nTPxPkKUGeEtQ/KxS3QnEr1D9ERERERETUP0RERERERNQ/XXTRRRdd1D92pF5H6nXUP6gEeUqQp9Q/wDQGTGPA1D/ANAZMY8DUP9lkk0022dQ/8pQgTwny1D8Lxa1Q3ArVPyT1OlKvI9U/PSXIU4I81T89JchTgjzVP1VVVVVVVdU/boXiVihu1T9uheJWKG7VP4e1b1j7htU/oOX8Wc6f1T+g5fxZzp/VP7kViluhuNU/0UUXXXTR1T/qdaReR+rVPwOmMWAaA9Y/HNa+Ye0b1j9ONtlkk03WP2ZmZmZmZtY/ZmZmZmZm1j9mZmZmZmbWP3+W82c5f9Y/mMaAaQyY1j/jVihuheLWP/uGtW9Y+9Y/FLdCcSsU1z8t589y/izXP0YXXXTRRdc/X0fqdaRe1z93d3d3d3fXP5CnBHlKkNc/qdeReh2p1z/CBx988MHXP8IHH3zwwdc/2zesfcPa1z/0Zzl/lvPXPwyYxoBpDNg/JchTgjwl2D8++OCDDz7YP3BY+4a1b9g/iYiIiIiI2D+66KKLLrrYP7rooosuutg/0xgwjQHT2D/sSL2O1OvYPwV5SpCnBNk/HanXkXod2T822WSTTTbZP08J8pQgT9k/TwnylCBP2T+BaQyYxoDZP5qZmZmZmdk/y/mznD/L2T/9Wc6f5fzZP/1Zzp/l/Nk/FopbobgV2j8vuuiiiy7aPy+66KKLLto/L7rooosu2j8vuuiiiy7aP0fqdaReR9o/YBoDpjFg2j+Seh2p15HaP6uqqqqqqto/w9o3rH3D2j/1OlKvI/XaPw5r37D2Dds/QMv5s5w/2z9Y+4a1b1jbP1j7hrVvWNs/WPuGtW9Y2z9xKxS3QnHbP4pbobgVits/o4suuuii2z/V60i9jtTbPwZMY8A0Btw/BkxjwDQG3D8ffPDBBx/cPzisfcPaN9w/UdwKxa1Q3D9qDJjGgGncP5tssskmm9w/m2yyySab3D+bbLLJJpvcP7ScP8v5s9w/tJw/y/mz3D+0nD/L+bPcP83MzMzMzNw/5vxZzp/l3D/+LOfPcv7cPxdddNFFF90/F1100UUX3T8wjQHTGDDdP0m9jtTrSN0/ex2p15F63T97HanXkXrdP5NNNtlkk90/rH3D2jes3T+sfcPaN6zdP8WtUNwKxd0/xa1Q3ArF3T/FrVDcCsXdP8WtUNwKxd0/3t3d3d3d3T/3DWvfsPbdPxA++OCDD94/KG6F4lYo3j8oboXiVijeP0GeEuQpQd4/c/4s589y3j+MLrroooveP4wuuuiii94/pF5H6nWk3j+9jtTrSL3eP9a+Ye0b1t4/1r5h7RvW3j/v7u7u7u7eP+/u7u7u7t4/7+7u7u7u3j8IH3zwwQffPyFPCfKUIN8/IU8J8pQg3z8hTwnylCDfPzl/lvNnOd8/OX+W82c53z9SryP1OlLfP1KvI/U6Ut8/a9+w9g1r3z+dP8v5s5zfP50/y/mznN8/tm9Y+4a13z/nz3L+LOffP+fPcv4s598/DJjGgGkM4D8ZMI0B0xjgPzJgGgOmMeA/MmAaA6Yx4D8++OCDDz7gPz744IMPPuA/SpCnBHlK4D9KkKcEeUrgP1coboXiVuA/VyhuheJW4D9XKG6F4lbgP1coboXiVuA/Y

bokeh.models.renderers.GlyphRenderer(
    id='e6f9105d-10b9-48a4-b1c3-6e9704059f34',
    data_source=bokeh.models.sources.ColumnDataSource(
        id='327d1591-e4d0-434b-9c9f-7540734f2865',
        callback=None,
        data={'y_ours': {'__ndarray__': 'AAAAAAAAAADTGDCNAdNYP9MYMI0B02g/nhLkKUGecj/TGDCNAdN4PwgffPDBB38/nhLkKUGegj+5FYpbobiFP9MYMI0B04g/7RvWvmHtiz8IH3zwwQePP54S5ClBnpI/KxS3QnErlD9GF1100UWXP9MYMI0B05g/YBoDpjFgmj/tG9a+Ye2bP3sdqdeRep0/CB988MEHnz9KkKcEeUqgPxEREREREaE/2JF6HanXoT+eEuQpQZ6iP2WTTTbZZKM/KxS3QnErpD/ylCBPCfKkP7kViluhuKU/f5bzZzl/pj9GF1100UWnPwyYxoBpDKg/0xgwjQHTqD9gGgOmMWCqPyebbLLJJqs/7RvWvmHtqz+0nD/L+bOsP3sdqdeReq0/zp/l/FnOrz9KkKcEeUqwPxEREREREbE/dNFFF110sT/YkXodqdexPztSryP1OrI/AtMYMI0Bsz9lk0022WSzP8hTgjwlyLM/KxS3QnErtD+P1OtIvY60P/KUIE8J8rQ/VVVVVVVVtT+5FYpbobi1P3+W82c5f7Y/41YoboXitj9GF1100UW3P6nXkXodqbc/DJjGgGkMuD9wWPuGtW+4P9MYMI0B07g/Ntlkk002uT+amZmZmZm5P2AaA6YxYLo/w9o3rH3Duj8nm2yyySa7P4pbobgVirs/7RvWvmHtuz9R3ArFrVC8P7ScP8v5s7w/F1100UUXvT97HanXkXq9P97d3d3d3b0/QZ4S5ClBvj+kXkfqdaS+PwgffPDBB78/a9+w9g1rvz/On+X8Wc6/P0qQpwR5SsA/fPDBBx98wD+uUNwKxa3AP9+w9g1r38A/ERERERERwT9DcSsUt0LBP3TRRRdddME/pjFgGgOmwT/YkXodqdfBPwnylCBPCcI/O1KvI/U6wj9tsskmm2zCP54S5ClBnsI/0HL+LOfPwj8C0xgwjQHDPzMzMzMzM8M/ZZNNNtlkwz/IU4I8JcjDP/qznD/L+cM/KxS3QnErxD9ddNFFF13EP4/U60i9jsQ/wDQGTGPAxD/ylCBPCfLEPyT1OlKvI8U/VVVVVVVVxT+HtW9Y+4bFP7kViluhuMU/6nWkXkfqxT8c1r5h7RvGP0422WSTTcY/f5bzZzl/xj+x9g1r37DGP+NWKG6F4sY/FLdCcSsUxz9GF1100UXHP6nXkXodqcc/2zesfcPaxz8MmMaAaQzIPz744IMPPsg/cFj7hrVvyD+huBWKW6HIP9MYMI0B08g/BXlKkKcEyT822WSTTTbJP2g5f5bzZ8k/aDl/lvNnyT+amZmZmZnJP8v5s5w/y8k//VnOn+X8yT8vuuiiiy7KP2AaA6YxYMo/knodqdeRyj/D2jesfcPKP/U6Uq8j9co/J5tssskmyz9Y+4a1b1jLP4pbobgViss/vLu7u7u7yz/tG9a+Ye3LPx988MEHH8w/UdwKxa1QzD+CPCXIU4LMP7ScP8v5s8w/5vxZzp/lzD8XXXTRRRfNP0m9jtTrSM0/ex2p15F6zT+sfcPaN6zNP97d3d3d3c0/ED744IMPzj9BnhLkKUHOP3P+LOfPcs4/pF5H6nWkzj/WvmHtG9bOPwgffPDBB88/OX+W82c5zz9r37D2DWvPP50/y/mznM8/zp/l/FnOzz8AAAAAAADQPxkwjQHTGNA/MmAaA6Yx0D9KkKcEeUrQP2PANAZMY9A/Y8A0Bkxj0D988MEHH3zQP5UgTwnylNA/lSBPCfKU0D+uUNwKxa3QP8eAaQyYxtA/37D2DWvf0D/44IMPPvjQP/jggw8++NA/ERERERER0T8RERERERHRPypBnhLkKdE/Q3ErFLdC0T9cobgVilvRP3TRRRdddNE/jQHTGDCN0T+mMWAaA6bRP79h7RvWvtE/2JF6HanX0T8J8pQgTwnSP1SCPCXIU9I/bbLJJpts0j+F4lYoboXSP54S5ClBntI/0HL+LOfP0j/poosuuujSPwLTGDCNAdM/GgOmMWAa0z8aA6YxYBrTPzMzMzMzM9M/TGPANAZM0z9MY8A0BkzTP2WTTTbZZNM/fsPaN6x90z+vI/U6Uq/TP8hTgjwlyNM/4YMPPvjg0z/6s5w/y/nTPxPkKUGeEtQ/KxS3QnEr1D9ERERERETUP0RERERERNQ/XXTRRRdd1D92pF5H6nXUP6gEeUqQp9Q/wDQGTGPA1D/ANAZMY8DUP9lkk0022dQ/8pQgTwny1D8Lxa1Q3ArVPyT1OlKvI9U/PSXIU4I81T89JchTgjzVP1VVVVVVVdU/boXiVihu1T9uheJWKG7VP4e1b1j7htU/oOX8Wc6f1T+g5fxZzp/VP7kViluhuNU/0UUXXXTR1T/qdaReR+rVPwOmMWAaA9Y/HNa+Ye0b1j9ONtlkk03WP2ZmZmZmZtY/ZmZmZmZm1j9mZmZmZmbWP3+W82c5f9Y/mMaAaQyY1j/jVihuheLWP/uGtW9Y+9Y/FLdCcSsU1z8t589y/izXP0YXXXTRRdc/X0fqdaRe1z93d3d3d3fXP5CnBHlKkNc/qdeReh2p1z/CBx988MHXP8IHH3zwwdc/2zesfcPa1z/0Zzl/lvPXPwyYxoBpDNg/JchTgjwl2D8++OCDDz7YP3BY+4a1b9g/iYiIiIiI2D+66KKLLrrYP7rooosuutg/0xgwjQHT2D/sSL2O1OvYPwV5SpCnBNk/HanXkXod2T822WSTTTbZP08J8pQgT9k/TwnylCBP2T+BaQyYxoDZP5qZmZmZmdk/y/mznD/L2T/9Wc6f5fzZP/1Zzp/l/Nk/FopbobgV2j8vuuiiiy7aPy+66KKLLto/L7rooosu2j8vuuiiiy7aP0fqdaReR9o/YBoDpjFg2j+Seh2p15HaP6uqqqqqqto/w9o3rH3D2j/1OlKvI/XaPw5r37D2Dds/QMv5s5w/2z9Y+4a1b1jbP1j7hrVvWNs/WPuGtW9Y2z9xKxS3QnHbP4pbobgVits/o4suuuii2z/V60i9jtTbPwZMY8A0Btw/BkxjwDQG3D8ffPDBBx/cPzisfcPaN9w/UdwKxa1Q3D9qDJjGgGncP5tssskmm9w/m2yyySab3D+bbLLJJpvcP7ScP8v5s9w/tJw/y/mz3D+0nD/L+bPcP83MzMzMzNw/5vxZzp/l3D/+LOfPcv7cPxdddNFFF90/F1100UUX3T8wjQHTGDDdP0m9jtTrSN0/ex2p15F63T97HanXkXrdP5NNNtlkk90/rH3D2jes3T+sfcPaN6zdP8WtUNwKxd0/xa1Q3ArF3T/FrVDcCsXdP8WtUNwKxd0/3t3d3d3d3T/3DWvfsPbdPxA++OCDD94/KG6F4lYo3j8oboXiVijeP0GeEuQpQd4/c/4s589y3j+MLrroooveP4wuuuiii94/pF5H6nWk3j+9jtTrSL3eP9a+Ye0b1t4/1r5h7RvW3j/v7u7u7u7eP+/u7u7u7t4/7+7u7u7u3j8IH3zwwQffPyFPCfKUIN8/IU8J8pQg3z8hTwnylCDfPzl/lvNnOd8/OX+W82c53z9SryP1OlLfP1KvI/U6Ut8/a9+w9g1r3z+dP8v5s5zfP50/y/mznN8/tm9Y+4a13z/nz3L+LOffP+fPcv4s598/DJjGgGkM4D8ZMI0B0xjgPzJgGgOmMeA/MmAaA6Yx4D8++OCDDz7gPz744IMPPuA/SpCnBHlK4D9KkKcEeUrgP1coboXiVuA/VyhuheJW4D9XKG6F4lbgP1coboXiVuA/Y

bokeh.models.renderers.GlyphRenderer(
    id='3e059d9b-1e99-4435-ad70-3c6ee47dc01e',
    data_source=bokeh.models.sources.ColumnDataSource(
        id='327d1591-e4d0-434b-9c9f-7540734f2865',
        callback=None,
        data={'y_ours': {'__ndarray__': 'AAAAAAAAAADTGDCNAdNYP9MYMI0B02g/nhLkKUGecj/TGDCNAdN4PwgffPDBB38/nhLkKUGegj+5FYpbobiFP9MYMI0B04g/7RvWvmHtiz8IH3zwwQePP54S5ClBnpI/KxS3QnErlD9GF1100UWXP9MYMI0B05g/YBoDpjFgmj/tG9a+Ye2bP3sdqdeRep0/CB988MEHnz9KkKcEeUqgPxEREREREaE/2JF6HanXoT+eEuQpQZ6iP2WTTTbZZKM/KxS3QnErpD/ylCBPCfKkP7kViluhuKU/f5bzZzl/pj9GF1100UWnPwyYxoBpDKg/0xgwjQHTqD9gGgOmMWCqPyebbLLJJqs/7RvWvmHtqz+0nD/L+bOsP3sdqdeReq0/zp/l/FnOrz9KkKcEeUqwPxEREREREbE/dNFFF110sT/YkXodqdexPztSryP1OrI/AtMYMI0Bsz9lk0022WSzP8hTgjwlyLM/KxS3QnErtD+P1OtIvY60P/KUIE8J8rQ/VVVVVVVVtT+5FYpbobi1P3+W82c5f7Y/41YoboXitj9GF1100UW3P6nXkXodqbc/DJjGgGkMuD9wWPuGtW+4P9MYMI0B07g/Ntlkk002uT+amZmZmZm5P2AaA6YxYLo/w9o3rH3Duj8nm2yyySa7P4pbobgVirs/7RvWvmHtuz9R3ArFrVC8P7ScP8v5s7w/F1100UUXvT97HanXkXq9P97d3d3d3b0/QZ4S5ClBvj+kXkfqdaS+PwgffPDBB78/a9+w9g1rvz/On+X8Wc6/P0qQpwR5SsA/fPDBBx98wD+uUNwKxa3AP9+w9g1r38A/ERERERERwT9DcSsUt0LBP3TRRRdddME/pjFgGgOmwT/YkXodqdfBPwnylCBPCcI/O1KvI/U6wj9tsskmm2zCP54S5ClBnsI/0HL+LOfPwj8C0xgwjQHDPzMzMzMzM8M/ZZNNNtlkwz/IU4I8JcjDP/qznD/L+cM/KxS3QnErxD9ddNFFF13EP4/U60i9jsQ/wDQGTGPAxD/ylCBPCfLEPyT1OlKvI8U/VVVVVVVVxT+HtW9Y+4bFP7kViluhuMU/6nWkXkfqxT8c1r5h7RvGP0422WSTTcY/f5bzZzl/xj+x9g1r37DGP+NWKG6F4sY/FLdCcSsUxz9GF1100UXHP6nXkXodqcc/2zesfcPaxz8MmMaAaQzIPz744IMPPsg/cFj7hrVvyD+huBWKW6HIP9MYMI0B08g/BXlKkKcEyT822WSTTTbJP2g5f5bzZ8k/aDl/lvNnyT+amZmZmZnJP8v5s5w/y8k//VnOn+X8yT8vuuiiiy7KP2AaA6YxYMo/knodqdeRyj/D2jesfcPKP/U6Uq8j9co/J5tssskmyz9Y+4a1b1jLP4pbobgViss/vLu7u7u7yz/tG9a+Ye3LPx988MEHH8w/UdwKxa1QzD+CPCXIU4LMP7ScP8v5s8w/5vxZzp/lzD8XXXTRRRfNP0m9jtTrSM0/ex2p15F6zT+sfcPaN6zNP97d3d3d3c0/ED744IMPzj9BnhLkKUHOP3P+LOfPcs4/pF5H6nWkzj/WvmHtG9bOPwgffPDBB88/OX+W82c5zz9r37D2DWvPP50/y/mznM8/zp/l/FnOzz8AAAAAAADQPxkwjQHTGNA/MmAaA6Yx0D9KkKcEeUrQP2PANAZMY9A/Y8A0Bkxj0D988MEHH3zQP5UgTwnylNA/lSBPCfKU0D+uUNwKxa3QP8eAaQyYxtA/37D2DWvf0D/44IMPPvjQP/jggw8++NA/ERERERER0T8RERERERHRPypBnhLkKdE/Q3ErFLdC0T9cobgVilvRP3TRRRdddNE/jQHTGDCN0T+mMWAaA6bRP79h7RvWvtE/2JF6HanX0T8J8pQgTwnSP1SCPCXIU9I/bbLJJpts0j+F4lYoboXSP54S5ClBntI/0HL+LOfP0j/poosuuujSPwLTGDCNAdM/GgOmMWAa0z8aA6YxYBrTPzMzMzMzM9M/TGPANAZM0z9MY8A0BkzTP2WTTTbZZNM/fsPaN6x90z+vI/U6Uq/TP8hTgjwlyNM/4YMPPvjg0z/6s5w/y/nTPxPkKUGeEtQ/KxS3QnEr1D9ERERERETUP0RERERERNQ/XXTRRRdd1D92pF5H6nXUP6gEeUqQp9Q/wDQGTGPA1D/ANAZMY8DUP9lkk0022dQ/8pQgTwny1D8Lxa1Q3ArVPyT1OlKvI9U/PSXIU4I81T89JchTgjzVP1VVVVVVVdU/boXiVihu1T9uheJWKG7VP4e1b1j7htU/oOX8Wc6f1T+g5fxZzp/VP7kViluhuNU/0UUXXXTR1T/qdaReR+rVPwOmMWAaA9Y/HNa+Ye0b1j9ONtlkk03WP2ZmZmZmZtY/ZmZmZmZm1j9mZmZmZmbWP3+W82c5f9Y/mMaAaQyY1j/jVihuheLWP/uGtW9Y+9Y/FLdCcSsU1z8t589y/izXP0YXXXTRRdc/X0fqdaRe1z93d3d3d3fXP5CnBHlKkNc/qdeReh2p1z/CBx988MHXP8IHH3zwwdc/2zesfcPa1z/0Zzl/lvPXPwyYxoBpDNg/JchTgjwl2D8++OCDDz7YP3BY+4a1b9g/iYiIiIiI2D+66KKLLrrYP7rooosuutg/0xgwjQHT2D/sSL2O1OvYPwV5SpCnBNk/HanXkXod2T822WSTTTbZP08J8pQgT9k/TwnylCBP2T+BaQyYxoDZP5qZmZmZmdk/y/mznD/L2T/9Wc6f5fzZP/1Zzp/l/Nk/FopbobgV2j8vuuiiiy7aPy+66KKLLto/L7rooosu2j8vuuiiiy7aP0fqdaReR9o/YBoDpjFg2j+Seh2p15HaP6uqqqqqqto/w9o3rH3D2j/1OlKvI/XaPw5r37D2Dds/QMv5s5w/2z9Y+4a1b1jbP1j7hrVvWNs/WPuGtW9Y2z9xKxS3QnHbP4pbobgVits/o4suuuii2z/V60i9jtTbPwZMY8A0Btw/BkxjwDQG3D8ffPDBBx/cPzisfcPaN9w/UdwKxa1Q3D9qDJjGgGncP5tssskmm9w/m2yyySab3D+bbLLJJpvcP7ScP8v5s9w/tJw/y/mz3D+0nD/L+bPcP83MzMzMzNw/5vxZzp/l3D/+LOfPcv7cPxdddNFFF90/F1100UUX3T8wjQHTGDDdP0m9jtTrSN0/ex2p15F63T97HanXkXrdP5NNNtlkk90/rH3D2jes3T+sfcPaN6zdP8WtUNwKxd0/xa1Q3ArF3T/FrVDcCsXdP8WtUNwKxd0/3t3d3d3d3T/3DWvfsPbdPxA++OCDD94/KG6F4lYo3j8oboXiVijeP0GeEuQpQd4/c/4s589y3j+MLrroooveP4wuuuiii94/pF5H6nWk3j+9jtTrSL3eP9a+Ye0b1t4/1r5h7RvW3j/v7u7u7u7eP+/u7u7u7t4/7+7u7u7u3j8IH3zwwQffPyFPCfKUIN8/IU8J8pQg3z8hTwnylCDfPzl/lvNnOd8/OX+W82c53z9SryP1OlLfP1KvI/U6Ut8/a9+w9g1r3z+dP8v5s5zfP50/y/mznN8/tm9Y+4a13z/nz3L+LOffP+fPcv4s598/DJjGgGkM4D8ZMI0B0xjgPzJgGgOmMeA/MmAaA6Yx4D8++OCDDz7gPz744IMPPuA/SpCnBHlK4D9KkKcEeUrgP1coboXiVuA/VyhuheJW4D9XKG6F4lbgP1coboXiVuA/Y

Loading BokehJS ...

In [21]:
df_p_imp = pd.DataFrame([pid_test, y_predicted]).T
df_p_imp.columns = ["patientunitstayid","predictedicumortality_imp"]

pid_common = set(pid_test) & set (pre_pid)
y_predicted = df_p[df_p.apply(lambda x : x.patientunitstayid in pid_common, axis=1)].predictedicumortality
y_predicted_imp = df_p_imp[df_p_imp.apply(lambda x : x.patientunitstayid in pid_common, axis=1)].predictedicumortality_imp
df_p_merge = pd.merge(df_p, df_p_imp, on="patientunitstayid")


#========================================
#  Draw scatter
#========================================
def plot_check(df_p):
    # DataFrame
    apache_IV = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IV"][['patientunitstayid', 'predictedicumortality','actualicumortality']]
    apache_IVa = eICU_file['apachePatientResult'][eICU_file['apachePatientResult']["apacheversion"]=="IVa"][['patientunitstayid', 'predictedicumortality']]
    df_IV_IVa = pd.merge(apache_IV, apache_IVa, on="patientunitstayid")
    df_p_IV_IVa = pd.merge(df_IV_IVa, df_p, on="patientunitstayid")
    

    # Graph title
    graph_title = ["IV vs IVa", "IV vs Ours", "IVa vs Ours", "IV vs imp", "IV vs imp", "imp vs Ours"]

    # Axis labels
    x_axis_label = ["APACHE IV", "APACHE IV", "APACHE IVa", "APACHE IV", "APACHE IV", "Ours"]
    y_axis_label = ["APACHE IVa", "Ours", "Ours"," Imputation", "Imputation", "Imputation"]

    # Graph data
    x_data = [df_p_IV_IVa.predictedicumortality_x,
              df_p_IV_IVa.predictedicumortality_x,
              df_p_IV_IVa.predictedicumortality_y,
              df_p_IV_IVa.predictedicumortality_x,
              df_p_IV_IVa.predictedicumortality_x,
              df_p_IV_IVa.predictedicumortality
             ]
    y_data = [df_p_IV_IVa.predictedicumortality_y,
              df_p_IV_IVa.predictedicumortality,
              df_p_IV_IVa.predictedicumortality,
              df_p_IV_IVa.predictedicumortality_imp,
              df_p_IV_IVa.predictedicumortality_imp,
              df_p_IV_IVa.predictedicumortality_imp
             ]
    
    # patientunitstayid
    pid = df_p_IV_IVa.patientunitstayid
    
    colormap = {'ALIVE': 'green', 'EXPIRED': 'red'}
    df_p_IV_IVa['color'] = df_p_IV_IVa['actualicumortality'].map(lambda x: colormap[x])

    
    output_notebook()

    p=[]
    
    for j in range(2):
        
        p.append([])
        
        for i in range(3):
                    
            # Other configurations
            x_size = 300
            y_size = 300
            alpha = 0.2
            size = 4

            # graph objects
            source = ColumnDataSource(data=dict(
                x=x_data[3*j+i],
                y=y_data[3*j+i], 
                pid=pid,
                color=df_p_IV_IVa['color'],
                legend=df_p_IV_IVa['actualicumortality']
            ))
                
            TOOLTIPS = [("index", "$index"),("(x,y)", "($x, $y)"),("pid", "@pid")]

            p[-1].append(figure(
                title = graph_title[3*j+i],
                plot_width = x_size,
                plot_height = y_size,
                tooltips = TOOLTIPS,
                x_range=(0, 1),
                y_range=(0, 1)
            ))
        
            p[-1][-1].xaxis.axis_label = x_axis_label[3*j+i]
            p[-1][-1].yaxis.axis_label = y_axis_label[3*j+i]
            p[-1][-1].circle(
                'x', 'y',
                fill_color="color",
                line_color="color",
                fill_alpha=alpha,
                legend='legend',
                size=size,
                source=source
            )

            # Texts
            description=Label(
                x_offset=10,
                y_offset=210,
                x_units='screen',
                y_units='screen',
                text=str(len(pid)) + " of patients plotted",
                text_font_size='1pt', render_mode="css"
            )
        
            p[-1][-1].add_layout(description)    
        
            p[-1][-1].legend.location = "top_left"
            p[-1][-1].legend.label_text_font_style = "bold"
            p[-1][-1].legend.label_text_font_size = "1pt"
            

    grid = gridplot(p)
    show(grid)
    
plot_check(df_p_merge)
    
    
# Calibration Plots
df_p_imp.columns = ["patientunitstayid","predictedicumortality"]
calibration_plot(df_p_imp)


# Confidence Interval
df_ci = pd.DataFrame(df_ci, columns=["Ours", "Imputation","Apache IV","Apache IVa"], index=["ALL"])
df_ci

Loading BokehJS ...

Loading BokehJS ...

Ours         Imputation            Apache IV  \
ALL  0.903 [0.887,0.919]  0.84 [0.821,0.86]  0.778 [0.752,0.803]   

            Apache IVa  
ALL  0.774 [0.748,0.8]